In [1]:
import pandas as pd
import numpy as np
import spacy
import re
from spacy.tokenizer import Tokenizer
from sklearn.feature_extraction.text import CountVectorizer
#from torchtext.data.utils import get_tokenizer
#from torchtext.vocab import build_vocab_from_iterator
import tensorflow as tf
from datasets import load_dataset

from tensorflow.keras import Sequential
from tensorflow.keras.layers import Dense, Embedding, GlobalAveragePooling1D
from tensorflow.keras.layers.experimental.preprocessing import TextVectorization

In [2]:
from transformers import BertModel, BertConfig,BertTokenizer
from transformers.models.bert.modeling_bert import BertForPreTrainingOutput

In [3]:
configuration = BertConfig()
print(configuration)
model = BertModel(configuration)
print(model)
config = model.config    
print(config)

BertConfig {
  "attention_probs_dropout_prob": 0.1,
  "classifier_dropout": null,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.1,
  "hidden_size": 768,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "max_position_embeddings": 512,
  "model_type": "bert",
  "num_attention_heads": 12,
  "num_hidden_layers": 12,
  "pad_token_id": 0,
  "position_embedding_type": "absolute",
  "transformers_version": "4.11.3",
  "type_vocab_size": 2,
  "use_cache": true,
  "vocab_size": 30522
}

BertModel(
  (embeddings): BertEmbeddings(
    (word_embeddings): Embedding(30522, 768, padding_idx=0)
    (position_embeddings): Embedding(512, 768)
    (token_type_embeddings): Embedding(2, 768)
    (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
    (dropout): Dropout(p=0.1, inplace=False)
  )
  (encoder): BertEncoder(
    (layer): ModuleList(
      (0): BertLayer(
        (attention): BertAttention(
          (self): BertSelfAttention(
            

In [5]:

#dataset = load_dataset(
#   'imdb')


#dataset['train'].to_csv('imdb_train.csv')
#dataset['test'].to_csv('imdb_test.csv')

Reusing dataset imdb (C:\Users\Aris\.cache\huggingface\datasets\imdb\plain_text\1.0.0\2fdd8b9bcadd6e7055e742a706876ba43f19faee861df134affd7a3f60fc38a1)


  0%|          | 0/3 [00:00<?, ?it/s]

Creating CSV from Arrow format:   0%|          | 0/3 [00:00<?, ?ba/s]

Creating CSV from Arrow format:   0%|          | 0/3 [00:00<?, ?ba/s]

32686819

In [4]:
dataset['train'][0]

NameError: name 'dataset' is not defined

In [5]:
df_train = pd.read_csv('imdb_train.csv')
df_test = pd.read_csv('imdb_test.csv')

print(df_train.head(10))
print(df_test.head(10))

   Unnamed: 0                                               text  label
0           0  I rented I AM CURIOUS-YELLOW from my video sto...      0
1           1  "I Am Curious: Yellow" is a risible and preten...      0
2           2  If only to avoid making this type of film in t...      0
3           3  This film was probably inspired by Godard's Ma...      0
4           4  Oh, brother...after hearing about this ridicul...      0
5           5  I would put this at the top of my list of film...      0
6           6  Whoever wrote the screenplay for this movie ob...      0
7           7  When I first saw a glimpse of this movie, I qu...      0
8           8  Who are these "They"- the actors? the filmmake...      0
9           9  This is said to be a personal film for Peter B...      0
   Unnamed: 0                                               text  label
0           0  I love sci-fi and am willing to put up with a ...      0
1           1  Worth the entertainment value of a rental, esp...

In [6]:
df_train['label'].value_counts()

1    12500
0    12500
Name: label, dtype: int64

In [7]:
df_test['label'].value_counts()

1    12500
0    12500
Name: label, dtype: int64

In [8]:
df_train

Unnamed: 0                                               text  label
0               0  I rented I AM CURIOUS-YELLOW from my video sto...      0
1               1  "I Am Curious: Yellow" is a risible and preten...      0
2               2  If only to avoid making this type of film in t...      0
3               3  This film was probably inspired by Godard's Ma...      0
4               4  Oh, brother...after hearing about this ridicul...      0
...           ...                                                ...    ...
24995        4995  A hit at the time but now better categorised a...      1
24996        4996  I love this movie like no other. Another time ...      1
24997        4997  This film and it's sequel Barry Mckenzie holds...      1
24998        4998  'The Adventures Of Barry McKenzie' started lif...      1
24999        4999  The story centers around Barry McKenzie who mu...      1

[25000 rows x 3 columns]

In [9]:
df_train['text'].to_csv("df_train.txt",index=False,header=True)


In [43]:
df_input = pd.read_csv("df_train.txt",delimiter="\t")
print(len(df_input))
print(df_input.iloc[0,:])

25000
text    I rented I AM CURIOUS-YELLOW from my video sto...
Name: 0, dtype: object


In [33]:
vocab = BertForPreTrainingOutput()
print(vocab)
token = BertTokenizer("df_train.txt")
print(token)

BertForPreTrainingOutput(loss=None, prediction_logits=None, seq_relationship_logits=None, hidden_states=None, attentions=None)
PreTrainedTokenizer(name_or_path='', vocab_size=24905, model_max_len=1000000000000000019884624838656, is_fast=False, padding_side='right', special_tokens={'unk_token': '[UNK]', 'sep_token': '[SEP]', 'pad_token': '[PAD]', 'cls_token': '[CLS]', 'mask_token': '[MASK]'})


In [28]:
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')


In [46]:
max_length = 128
print(len(df_input))
for i in range(len(df_input)):
    print(df_input.iloc[i,:])
    inputs = tokenizer.encode_plus(str(df_input.iloc[i,:]),add_special_tokens=True,
            pad_to_max_length=True,
            return_attention_mask=True,
            return_tensors="pt")
    ID.append(inputs.get('input_ids'))
    Masks.append(input.get('attention_mask'))
    return ID,Masks

25000
text    I rented I AM CURIOUS-YELLOW from my video sto...
Name: 0, dtype: object
{'input_ids': tensor([[  101,  3793,  1045, 12524,  1045,  2572,  8025,  1011,  3756,  2013,
          2026,  2678,  2358,  2080,  1012,  1012,  1012,  2171,  1024,  1014,
          1010, 26718, 18863,  1024,  4874,   102]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
         1, 1]])}
text    "I Am Curious: Yellow" is a risible and preten...
Name: 1, dtype: object
{'input_ids': tensor([[  101,  3793,  1000,  1045,  2572,  8025,  1024,  3756,  1000,  2003,
          1037, 15544, 19307,  1998,  3653,  6528,  1012,  1012,  1012,  2171,
          1024,  1015,  1010, 26718, 18863,  1024,  4874,   102]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0]]), 'attentio

{'input_ids': tensor([[  101,  3793,  2428,  1010,  1045,  2064,  1005,  1056,  2903,  2008,
          1045,  2985,  1002,  1019,  2006, 16215,  2072,  1012,  1012,  1012,
          2171,  1024,  3486,  1010, 26718, 18863,  1024,  4874,   102]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
         1, 1, 1, 1, 1]])}
text    I rented this movie about 3 years ago, and it ...
Name: 36, dtype: object
{'input_ids': tensor([[  101,  3793,  1045, 12524,  2023,  3185,  2055,  1017,  2086,  3283,
          1010,  1998,  2009,  1012,  1012,  1012,  2171,  1024,  4029,  1010,
         26718, 18863,  1024,  4874,   102]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,

{'input_ids': tensor([[  101,  3793,  2023,  3185,  2196,  2081,  2009,  2000, 12370,  1999,
          2256, 12098,  1012,  1012,  1012,  2171,  1024,  5401,  1010, 26718,
         18863,  1024,  4874,   102]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]])}
text    I thought this was a very clunky, uninvolving ...
Name: 58, dtype: object
{'input_ids': tensor([[  101,  3793,  1045,  2245,  2023,  2001,  1037,  2200, 18856, 16814,
          2100,  1010,  4895,  2378,  6767, 25780,  1012,  1012,  1012,  2171,
          1024,  5388,  1010, 26718, 18863,  1024,  4874,   102]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
         1, 1, 1, 1]])}
text    Ned aKel

{'input_ids': tensor([[  101,  3793,  6548,  4477,  4227, 23215,  2005,  1996,  2755, 22794,
          1012,  1012,  1012,  2171,  1024,  3938,  1010, 26718, 18863,  1024,
          4874,   102]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]])}
text    This film seemed way too long even at only 75 ...
Name: 91, dtype: object
{'input_ids': tensor([[  101,  3793,  2023,  2143,  2790,  2126,  2205,  2146,  2130,  2012,
          2069,  4293,  1012,  1012,  1012,  2171,  1024,  6205,  1010, 26718,
         18863,  1024,  4874,   102]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]])}
text    Sexo Cannibal, or Devil Hunter as it's more co...
Name: 92, dtype: object
{'input_ids': tensor([[  101, 

{'input_ids': tensor([[  101,  3793,  2023,  2143,  2018,  1037,  2843,  1997,  4872,  1010,
          1998,  1996,  5436,  1059,  1012,  1012,  1012,  2171,  1024, 12567,
          1010, 26718, 18863,  1024,  4874,   102]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
         1, 1]])}
text    This is one of the dumbest films, I've ever se...
Name: 118, dtype: object
{'input_ids': tensor([[  101,  3793,  2023,  2003,  2028,  1997,  1996, 12873,  4355,  3152,
          1010,  1045,  1005,  2310,  2412,  7367,  1012,  1012,  1012,  2171,
          1024, 12963,  1010, 26718, 18863,  1024,  4874,   102]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1

...

{'input_ids': tensor([[  101,  3793,  2023,  3185,  2003,  2061,  3375,  2008,  2009,  2064,
          2022,  2445,  1012,  1012,  1012,  2171,  1024, 14078, 24087,  1010,
         26718, 18863,  1024,  4874,   102]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
         1]])}
text    ** possible spoilers **<br /><br />I like this...
Name: 13256, dtype: object
{'input_ids': tensor([[  101,  3793,  1008,  1008,  2825, 27594,  2545,  1008,  1008,  1026,
          7987,  1013,  1028,  1026,  7987,  1013,  1028,  1045,  2066,  2023,
          1012,  1012,  1012,  2171,  1024, 14078, 26976,  1010, 26718, 18863,
          1024,  4874,   102]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1

{'input_ids': tensor([[  101,  3793,  1045,  3876,  2067,  2000,  3422,  1000,  3191,  2026,
          2970,  1010,  1000,  1037, 20228,  4017,  1012,  1012,  1012,  2171,
          1024, 14078, 17914,  1010, 26718, 18863,  1024,  4874,   102]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
         1, 1, 1, 1, 1]])}
text    I picked this one up on a whim from the librar...
Name: 13281, dtype: object
{'input_ids': tensor([[  101,  3793,  1045,  3856,  2023,  2028,  2039,  2006,  1037,  1059,
         14341,  2013,  1996,  5622, 10024,  2099,  1012,  1012,  1012,  2171,
          1024, 14078,  2620,  2487,  1010, 26718, 18863,  1024,  4874,   102]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 

{'input_ids': tensor([[  101,  3793,  1000,  1996, 22640,  7983,  1000,  3340,  9267, 10243,
          7229,  2004,  1037,  5296,  1012,  1012,  1012,  2171,  1024, 14506,
         10790,  1010, 26718, 18863,  1024,  4874,   102]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
         1, 1, 1]])}
text    THE MATADOR is hit-man movie lite....if you ca...
Name: 13311, dtype: object
{'input_ids': tensor([[  101,  3793,  1996, 22640,  7983,  2003,  2718,  1011,  2158,  3185,
          5507,  2063,  1012,  1012,  1012,  1012,  2065,  2017,  6187,  1012,
          1012,  1012,  2171,  1024, 14506, 14526,  1010, 26718, 18863,  1024,
          4874,   102]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 

Name: 13331, dtype: object


KeyboardInterrupt: 